In [1]:
import pycaret
import pandas as pd
from pycaret.classification import *
pycaret.__version__


'3.3.2'

In [2]:
def process_dataframe(df):
    # Extract columns that contain only numeric values
    numeric_cols = df.select_dtypes(include=[float, int]).columns.tolist()
    
    # Check if 'species_name' and 'set' columns exist in the DataFrame
    other_cols = ['species_name']
    for col in other_cols:
        if col not in df.columns:
            raise ValueError(f"Column '{col}' does not exist in the DataFrame")
    
    # Merge numeric columns and other specified columns
    selected_cols = numeric_cols + other_cols
    
    # Create a new DataFrame
    new_df = df[selected_cols]
    
    return new_df

def split_dataset(csv_path):
    df = pd.read_csv(csv_path)
    train_val_set = df[df['set'].isin(['train', 'val'])]
    train_val_set = process_dataframe(train_val_set)  # The original data contains columns other than features and targets; this function removes them, retaining only features and targets.
    test_set = df[df['set'].isin(['test'])]
    test_set = process_dataframe(test_set)
    return train_val_set, test_set

In [3]:
import glob
import os
import time
import gc

csv_paths = glob.glob('./FusedFeatures/*.csv')

for csv_path in csv_paths:
    
    train_val_set, test_set = split_dataset(csv_path)
    
    exp = ClassificationExperiment()

    session_id = int(time.time())
    features_type = os.path.split(csv_path)[1].split('.')[0]
    
    exp.setup(train_val_set, target='species_name', session_id=session_id, normalize=True, pca=True,
              experiment_name=features_type, use_gpu=False)

    # models = ['gpc','gbc','lightgbm'] these models are very slow ,and performence not well in our preexperiment
    model_names = ['ridge', 'rbfsvm', 'lda', 'lr', 'mlp', 'rf', 'knn', 'nb', 'dt', 'svm', 'qda', 'ada', 'et', 'dummy']
    # model_names = ['catboost']
 
    trained_models = exp.compare_models(include=model_names, fold=5, n_select=14)

    save_folder = os.path.join('./models/cpu/', features_type)
    if not os.path.exists(save_folder):
        os.makedirs(save_folder)
    
    for trained_model in trained_models:
        model_name = trained_model.__class__.__name__

        # Predict using the trained model and save the prediction result
        predict_result_train_model = exp.predict_model(trained_model, test_set)
        predict_result_train_model.to_csv(os.path.join(save_folder, model_name + '_train.csv'))
        exp.save_model(trained_model, os.path.join(save_folder, model_name + '_train'))

        # Tune the model, predict using the tuned model, and save the prediction result
        tuned_model, tuner = exp.tune_model(trained_model, return_tuner=True, n_iter=20, fold=5, choose_better=True)
        predict_result_tune_model = exp.predict_model(tuned_model, test_set)
        predict_result_tune_model.to_csv(os.path.join(save_folder, model_name + '_tune.csv'))
        exp.save_model(tuned_model, os.path.join(save_folder, model_name + '_tune'))

        print(tuner)        

    exp.save_experiment(os.path.join(save_folder, 'experiment'))
    gc.collect()

Initiated  . . . . . . . . . . . . . . . . . .              18:11:52
Status     . . . . . . . . . . . . . . . . . .  Loading Dependencies
Estimator  . . . . . . . . . . . . . . . . . .     Compiling Library

Transformation Pipeline and Model Successfully Saved


Initiated  . . . . . . . . . . . . . . . . . .              18:19:03
Status     . . . . . . . . . . . . . . . . . .  Loading Dependencies
Estimator  . . . . . . . . . . . . . . . . . .     Compiling Library

Fitting 5 folds for each of 20 candidates, totalling 100 fits


Transformation Pipeline and Model Successfully Saved
RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=None, shuffle=False),
                   error_score=nan,
                   estimator=Pipeline(memory=Memory(location=None),
                                      steps=[('label_encoding',
                                              TransformerWrapperWithInverse(exclude=None,
                                                                            include=None,
                                                                            transformer=LabelEncoder())),
                                             ('numerical_imputer',
                                              TransformerWrapper(exclude=None,
                                                                 include=['0',
                                                                          '1',
                                                                          '2',
                         

...

Transformation Pipeline and Model Successfully Saved
RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=None, shuffle=False),
                   error_score=nan,
                   estimator=Pipeline(memory=Memory(location=None),
                                      steps=[('label_encoding',
                                              TransformerWrapperWithInverse(exclude=None,
                                                                            include=None,
                                                                            transformer=LabelEncoder())),
                                             ('numerical_imputer',
                                              TransformerWrapper(exclude=None,
                                                                 include=['0',
                                                                          '1',
                                                                          '2',
                         

Transformation Pipeline and Model Successfully Saved


Initiated  . . . . . . . . . . . . . . . . . .              11:53:43
Status     . . . . . . . . . . . . . . . . . .  Loading Dependencies
Estimator  . . . . . . . . . . . . . . . . . .     Compiling Library

Fitting 5 folds for each of 4 candidates, totalling 20 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Transformation Pipeline and Model Successfully Saved
GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=None, shuffle=False),
             error_score=nan,
             estimator=Pipeline(memory=Memory(location=None),
                                steps=[('label_encoding',
                                        TransformerWrapperWithInverse(exclude=None,
                                                                      include=None,
                                                                      transformer=LabelEncoder())),
                                       ('numerical_imputer',
                                        TransformerWrapper(exclude=None,
                                                           include=['0', '1',
                                                                    '2', '3',
                                                                    '4', '5',
                                                                    '6', '7',
    